# Setup and imports

In [ ]:
# Imports
import httpx
import time
import re
import csv

# API Config
API_TOKEN = "mytoken"  # Replace with your actual API token
HEADERS = {"Authorization": f"Bearer {API_TOKEN}"}
BASE_URL = "https://api.printify.com"
SHOP_ID = "myshopid"  # Replace with your actual shop ID

# Configure shared httpx timeout settings
TIMEOUT = httpx.Timeout(30.0, connect=10.0)

# Product Types to Search
product_types = ["mug", "hoodie", "tote bag", "bumper sticker", "t-shirt"]

# Fetch and Filter Catalog Products

In [6]:
# Fetch all blueprints from catalog
with httpx.Client() as client:
    response = client.get(f"{BASE_URL}/v1/catalog/blueprints.json", headers=HEADERS)
    products = response.json()
    print(f"Found {len(products)} total products.")

# Filter relevant product types
def detect_product_type(title, types):
    for t in types:
        if t in title.lower():
            return t
    return "other"

filtered_products = [
    {**p, "category": detect_product_type(p["title"], product_types)}
    for p in products
    if any(ptype in p["title"].lower() for ptype in product_types)
]

print(f"Found {len(filtered_products)} filtered products in product types: {product_types}.")

Found 1108 total products.
Found 171 filtered products in product types: ['mug', 'hoodie', 'tote bag', 'bumper sticker', 't-shirt'].


# Fetch Shipping Info
### Get Cheapest Standard Shipping (US Preferred, or Rest of World)

In [67]:
def cheapest_standard_us_shipping(blueprint_id, provider_id):
    resp = httpx.get(
        f"{BASE_URL}/v2/catalog/blueprints/{blueprint_id}/print_providers/{provider_id}/shipping.json",
        headers=HEADERS,
        timeout=TIMEOUT
    )

    shipping = resp.json()
    standard_url = shipping.get("links", {}).get("standard")
    if not standard_url:
        return {}

    resp = httpx.get(standard_url, headers=HEADERS, timeout=TIMEOUT)
    shipping_data = resp.json().get("data", [])

    cheapest = {}
    for entry in shipping_data:
        attr = entry.get("attributes", {})
        variant_id = attr.get("variantId")
        cost_info = attr.get("shippingCost", {})
        country = attr.get("country", {}).get("code")

        if not variant_id:
            continue

        existing = cheapest.get(variant_id)
        is_us = country == "US"
        is_better = (
            existing is None or
            (is_us and existing["country"] != "US") or
            (is_us and cost_info["firstItem"]["amount"] < existing["shippingCost"]["firstItem"]["amount"])
        )

        if is_us or country == "REST_OF_THE_WORLD":
            if is_better:
                cheapest[variant_id] = {
                    "variantId": variant_id,
                    "country": country,
                    "shippingPlanId": attr.get("shippingPlanId"),
                    "shippingCost": cost_info,
                    "handlingTime": attr.get("handlingTime"),
                }

    return cheapest

# Get Providers and Their Variants

In [ ]:
def get_providers_and_variants(blueprint_id):
    resp = httpx.get(f"{BASE_URL}/v1/catalog/blueprints/{blueprint_id}/print_providers.json", headers=HEADERS, timeout=TIMEOUT)
    if resp.status_code != 200:
        return None

    providers = resp.json()
    result = {}

    for provider in providers:
        provider_id = provider["id"]

        v_resp = httpx.get(
            f"{BASE_URL}/v1/catalog/blueprints/{blueprint_id}/print_providers/{provider_id}/variants.json",
            headers=HEADERS
        )
        location_resp = httpx.get(
            f"{BASE_URL}/v1/catalog/print_providers/{provider_id}.json",
            headers=HEADERS
        )

        if v_resp.status_code != 200 or location_resp.status_code != 200:
            continue

        variants = v_resp.json().get("variants", [])
        country = location_resp.json().get("location", {}).get("country", "Unknown")

        if variants:
            result[provider_id] = {
                "provider_name": provider["title"],
                "country": country,
                "variants": [{"variant_id": v["id"], "title": v["title"]} for v in variants]
            }

    return result


# Create Temporary Products

In [ ]:
def create_temp_products(product):
    provider_variants = get_providers_and_variants(product["id"])
    if not provider_variants:
        return None, None

    created_ids = []

    # Iterate through each provider and create a temporary product
    for provider_id, provider_data in provider_variants.items():
        limited_variants = provider_data["variants"][:100]  # ✅ consistent 100 variant limit
        variant_ids = [v["variant_id"] for v in limited_variants]

        print_areas = [{
            "variant_ids": variant_ids,
            "placeholders": [{
                "position": "front",
                "images": [{
                    "id": "6826f70020ff4c8b6b125c29",
                    "x": 0.5, "y": 0.5, "scale": 1, "angle": 0,
                    "pattern": {"spacing_x": 1, "spacing_y": 2, "scale": 3, "offset": 4, "angle": 0}
                }]
            }]
        }]

        body = {
            "title": f"TEMP: {product['title']} ({provider_id} - {provider_data['provider_name']})",
            "description": product.get("description", ""),
            "blueprint_id": product["id"],
            "print_provider_id": provider_id,
            "variants": [{"id": v["variant_id"], "price": 100} for v in limited_variants],
            "print_areas": print_areas,
            "images": [],
            "is_published": False
        }

        resp = httpx.post(f"{BASE_URL}/v1/shops/{SHOP_ID}/products.json", headers=HEADERS, json=body, timeout=TIMEOUT)
        if resp.status_code == 200:
            created_ids.append(resp.json()["id"])
        else:
            print(f"❌ Failed to create product {product["title"]} - {provider_id} ({resp.status_code}): {resp.text}")

    return created_ids if created_ids else None, provider_variants


# Fetch Pricing Info From Created Products in My Shop

In [ ]:
def fetch_pricing_info(product_id):
    response = httpx.get(f"{BASE_URL}/v1/shops/{SHOP_ID}/products/{product_id}.json", headers=HEADERS, timeout=TIMEOUT)
    if response.status_code != 200:
        return []

    data = response.json()
    variants = data.get("variants", [])
    result = []

    for variant in variants:
        provider_name = re.search(r"\(\d+\s*-\s*(.+?)\)", data["title"])
        provider_name = provider_name.group(1).strip() if provider_name else None

        result.append({
            "custom_title": data["title"],
            "blueprint_id": data["blueprint_id"],
            "print_provider_id": data["print_provider_id"],
            "print_provider_name": provider_name,
            "variant_id": variant["id"],
            "variant_title": variant.get("title", ""),
            "cost": variant.get("cost", 0) / 100,
            "created_product_id": product_id,
        })
    return result


# Main Loop: Build Pricing Dataset

In [69]:
# In case of errors, we can skip already processed products and rerun the main loop in the next cell
processed_product_ids = [] 

pricing_results = []
created_product_ids = []

In [70]:
for product in filtered_products:
    if product["id"] in processed_product_ids:
        print(f"Skipping already processed product: {product['title']} {product['id']}")
        continue
    
    print(f"\nCreating temp product(s) for: {product['title']}")
    product_ids, provider_variants = create_temp_products(product)
    print(f"Created product IDs: {product_ids}")

    if not product_ids:
        continue

    for pid in product_ids:
        created_product_ids.append(pid)
        time.sleep(1)
        
        try:
            variants = fetch_pricing_info(pid)
        except Exception as e:
            print(f"❌ Error fetching pricing info for product {pid}: {e}")
            continue

        try:
            shipping_map = cheapest_standard_us_shipping(
                variants[0]["blueprint_id"],
                variants[0]["print_provider_id"]
            )
        except Exception as e:
            print(f"❌ Error fetching shipping map for product {pid}: {e}")
            continue

        for variant in variants:
            provider_data = provider_variants.get(variant["print_provider_id"])
            shipping_info = shipping_map.get(variant["variant_id"])

            if not shipping_info:
                print(f"⚠️ Skipping variant {variant['variant_id']} — no US or Rest of World shipping")
                continue

            sc = shipping_info["shippingCost"]
            ht = shipping_info["handlingTime"]
            
            variant["source_product_title"] = product["title"]
            variant["print_provider_country"] = provider_data.get("country") if provider_data else None
            variant["shipping_first_item"] = sc["firstItem"]["amount"] / 100
            variant["shipping_additional_items"] = sc["additionalItems"]["amount"] / 100
            variant["shipping_to_country"] = shipping_info["country"]
            variant["handling_time_days"] = f"{ht.get('from', '')}-{ht.get('to', '')} days"

            pricing_results.append(variant)
    
    processed_product_ids.append(product["id"])

print(f"✅ Created {len(created_product_ids)} temporary products")

# Clean up created temp products           
for pid in created_product_ids:
    response = httpx.delete(f"{BASE_URL}/v1/shops/{SHOP_ID}/products/{pid}.json", headers=HEADERS, timeout=TIMEOUT)
    print(f"[DELETE {'✅' if response.status_code == 200 else '❌'}] ID {pid}")
    time.sleep(0.5)

# All products processed, reset processed list    
processed_product_ids = []


Creating temp product(s) for: Kids Hoodie
Created product IDs: ['68417c8bedf332d8500cccff', '68417c8e15e80fed7d0d3e1b', '68417c8f6f24db6250070892']
⚠️ Skipping variant 32207 — no US or Rest of World shipping
⚠️ Skipping variant 32117 — no US or Rest of World shipping

Creating temp product(s) for: Mug 11oz
Created product IDs: ['68417c96c8cd8066b7043d6d']

Creating temp product(s) for: Stainless Steel Travel Mug
Created product IDs: ['68417c9b091040232a020769']

Creating temp product(s) for: Unisex Full Zip Hoodie
Created product IDs: ['68417c9f78c37583d205a912', '68417ca0c8cd8066b7043d6e']

Creating temp product(s) for: Unisex College Hoodie
Created product IDs: ['68417ca7c8cd8066b7043d6f', '68417ca9c8cd8066b7043d70', '68417cab6f24db6250070899', '68417cad78c37583d205a914', '68417caf73341a387c073ceb', '68417cb2c8cd8066b7043d74', '68417cb378c37583d205a916', '68417cb56f24db625007089a', '68417cb6091040232a02076c']
⚠️ Skipping variant 34118 — no US or Rest of World shipping
⚠️ Skipping va

In [ ]:
# Additional debugging output
print(len(created_product_ids), "created_product_ids")
print(f"processed_product_ids: {len(processed_product_ids)}\n{processed_product_ids}")
print(pricing_results)
# for pid in created_product_ids:
#     response = httpx.delete(f"{BASE_URL}/v1/shops/{SHOP_ID}/products/{pid}.json", headers=HEADERS, timeout=TIMEOUT)
#     print(f"[DELETE {'✅' if response.status_code == 200 else '❌'}] ID {pid}")
#     time.sleep(0.5)

286 created_product_ids
67
processed_product_ids: 0
[]
[{'custom_title': 'TEMP: Kids Hoodie (6 - T Shirt and Sons)', 'blueprint_id': 67, 'print_provider_id': 6, 'print_provider_name': 'T Shirt and Sons', 'variant_id': 32103, 'variant_title': 'Arctic White / XS', 'cost': 24.52, 'created_product_id': '68417c8bedf332d8500cccff', 'source_product_title': 'Kids Hoodie', 'print_provider_country': 'GB', 'shipping_first_item': 22.79, 'shipping_additional_items': 6.19, 'shipping_to_country': 'REST_OF_THE_WORLD', 'handling_time_days': '10-30 days'}, {'custom_title': 'TEMP: Kids Hoodie (6 - T Shirt and Sons)', 'blueprint_id': 67, 'print_provider_id': 6, 'print_provider_name': 'T Shirt and Sons', 'variant_id': 32104, 'variant_title': 'Arctic White / S', 'cost': 24.52, 'created_product_id': '68417c8bedf332d8500cccff', 'source_product_title': 'Kids Hoodie', 'print_provider_country': 'GB', 'shipping_first_item': 22.79, 'shipping_additional_items': 6.19, 'shipping_to_country': 'REST_OF_THE_WORLD', 'han

# Save to CSV

In [ ]:
csv_filename = "results/pricing_results.csv"

# Get all unique keys across all variant entries to use as CSV headers
fieldnames = sorted({key for entry in pricing_results for key in entry.keys()})

with open(csv_filename, "w", newline="", encoding="utf-8") as f:
    writer = csv.DictWriter(f, fieldnames=fieldnames)
    writer.writeheader()
    writer.writerows(pricing_results)

print(f"✅ Saved pricing for {len(pricing_results)} variants to '{csv_filename}'.")

✅ Saved pricing for 16136 variants to 'pricing_results.csv'.


# Snippets

### Fetch image uploads from Printify to use in creating products

In [ ]:
with httpx.Client() as client:
    response = client.get(
        f"{BASE_URL}/v1/uploads.json",
        headers=HEADERS
    )
    image = response.json()
    print(f"Found {image}.")